In [1]:
from rank_bm25 import BM25Okapi
import pandas as pd
import numpy as np
import itertools
import os
import copy

In [2]:
len(wiki)

NameError: name 'wiki' is not defined

# wiki : id2context

In [4]:
corpus = pd.read_csv("../corpus_id.csv")
corpus.shape

(56366, 5)

In [5]:
corpus

_index _type    _id     _score  \
0      origin-wiki  _doc   6795  27.979990   
1      origin-wiki  _doc  14489  27.434950   
2      origin-wiki  _doc  52322  25.270552   
3      origin-wiki  _doc   2269  22.820520   
4      origin-wiki  _doc  20097  22.254482   
...            ...   ...    ...        ...   
56361  origin-wiki  _doc  24584   0.020687   
56362  origin-wiki  _doc  43489   0.020687   
56363  origin-wiki  _doc  15654   0.018875   
56364  origin-wiki  _doc    973   0.015869   
56365  origin-wiki  _doc  48439   0.015273   

                                                 _source  
0      {'document_text': '내각(內閣, cabinet)은 행정부의 주요 각료...  
1      {'document_text': '미국 상의원 또는 미국 상원(United Stat...  
2      {'document_text': '국회에 관해 규정하는 헌법 제4장의 첫 조문이다....  
3      {'document_text': '이하의 국가들은 의회에서 행정부 수반을 선출한다는...  
4      {'document_text': "미국의 외교정책의 수립과 이행에 대한 주된 책임을...  
...                                                  ...  
56361  {'document_text': "스타크래프트 ll : 프리미어 개인리그 준우승 2...  
56362  {'document_text': "1월\n* 1월 3일 (1010회) - 레드벨벳 ...  
56363  {'document_text': '파일:Insigne_Francisci.svg|프란...  
56364  {'document_text': ':참고 문헌 목록은 제1차 세계 대전의 서지 문서...  
56365  {'document_text': 'ImageSize = width:900 heigh...  

[56366 rows x 5 columns]

In [6]:
l = []
for i in range(corpus.shape[0]):
#     for j in range(corpus.shape[1]):
    l.append(corpus.iloc[i,[2,4]])
len(l)

56366

In [7]:
id2context = {x['_id']:eval(x['_source'])['document_text'] for x in l}

In [8]:
len(set(id2context.keys()))

56366

# 데이터 불러오기

In [14]:
origin = "/Users/youp/Desktop/Boostcamp/대회/competetion3/retrieval_ensemble"       # 현재 디렉토리

file_list = os.listdir(origin)
file_list.sort()
# file_list = file_list[1:-1]
file_list # 앙상블 후보 파일

['BM25_b0.55_k1.8.csv',
 'BM25_b6.5_k1.8.csv',
 'BM25_b6.5_k2.0.csv',
 'DFI_standardized.csv',
 'DFR_g_b_h2.csv',
 'IB_ll_ttf_h3.csv',
 'LMDirichlet_800.csv',
 'LMJelinekMercer_0.8.csv',
 'TFIDF.csv']

In [15]:
# 9개 파일 불러오기
# df_list : 9개의 데이터 프레임이 담긴 리스트
df_list = []
for i in range(len(file_list)):
    tmp = pd.read_csv(origin + f"/{file_list[i]}") ###
    df_list.append(tmp)
    
# 최초로 뽑아낸 context 후보의 개수
K = 30

In [16]:
len(df_list)

9

# m개의 파일 더해서 top k개의 context 뽑아내기

"context1 context2 ... contextk" 형식이 최종 아웃풋

1. 각 파일에서 각 query에 해당하는 확률 30개 별로 표준화(min-max, normalize -> softmax)
2. 같은 id 끼리는 확률 더하고, 아닌 애들은 그대로 놔둠<br>
   여기서 dict 이용하면 될듯 {id:prob}
3. 각 query 별로 최종 top k개 뽑아서 k개의 context 연결해서 output 만들기

* 2개의 파일 더하는 코드

1. 표준화

In [154]:
N=2
m=2
topk = 5

In [89]:
df1, df2 = df_list[0], df_list[1]

In [134]:
for i in range(df1.shape[0]):
    tmp = df1.iloc[i,]
    score = tmp[0:K]
    idx = tmp[K]
    # min-Max
    score_mM = (score - score.min()) / (score.max() - score.min())
#     df1.iloc[i,0:K] = score_mM
    # softmax
    df1.iloc[i,0:K] = pd.Series(map(np.exp, score_mM)) / np.sum(pd.Series(map(np.exp, score_mM)))
    
for i in range(df2.shape[0]):
    tmp = df2.iloc[i,]
    score = tmp[0:K]
    idx = tmp[K]
    # min-Max
    score_mM = (score - score.min()) / (score.max() - score.min())
#     df2.iloc[i,0:K] = score_mM
    # softmax
    df2.iloc[i,0:K] = pd.Series(map(np.exp, score_mM)) / np.sum(pd.Series(map(np.exp, score_mM)))

2. 두개 데이터 합

score를 dict로 다 더해서 가장 높은 확률을 갖는 id들을 뽑아내기

In [141]:
a = {}
a['a'] = 1
a

{'a': 1}

In [143]:
l_df = [df1, df2]
l_dict = []
for i in range(df1.shape[0]):
    tmp_dict = {}
    for j in range(m):
        idx = eval(l_df[j].iloc[i,K])
        for k in range(len(idx)):
            if idx[k] in tmp_dict.keys():
                tmp_dict[idx[k]] += l_df[j].iloc[i,k]
            else:
                tmp_dict[idx[k]] = l_df[j].iloc[i,k]
    l_dict.append(tmp_dict)
l_dict

[{'23174': 0.13523514609037185,
  '20220': 0.10507091309184774,
  '39471': 0.09151667507573873,
  '5978': 0.08566024438464934,
  '6706': 0.08216042358682313,
  '43271': 0.08228044351399966,
  '13717': 0.08263231917677247,
  '12176': 0.07441942729723128,
  '38446': 0.06883566991262037,
  '35326': 0.06744941351908286,
  '38434': 0.07004561077156929,
  '48948': 0.06532669084563628,
  '31256': 0.060866012959178345,
  '26967': 0.06078890272563082,
  '45355': 0.05826016541771044,
  '30236': 0.059622453358148045,
  '22606': 0.05723346458913314,
  '40823': 0.055305095064717015,
  '35322': 0.05574050983645667,
  '16189': 0.05574797155634768,
  '10327': 0.05517533023916785,
  '1454': 0.05560310502265993,
  '45958': 0.05521151617779014,
  '22205': 0.05287984252081139,
  '38450': 0.05246690576455727,
  '13224': 0.05181673355680502,
  '17232': 0.05201631769931818,
  '39475': 0.025114484291911692,
  '3203': 0.05017465876133713,
  '12179': 0.049884993898381275,
  '11493': 0.02545855929359459},
 {'162

3. query 별로 확률 높은 3개의 id 반환

In [158]:
# k개 가져오기
l_id = []
for i in range(len(l_dict)):
    tmp = sorted(l_dict[i].items(), key = lambda x: x[1], reverse = True)[0:topk]
    ids = [x[0] for x in tmp]
    l_id.append(ids)
l_id

[['23174', '20220', '39471', '5978', '13717'],
 ['16277', '9787', '1479', '8562', '24991'],
 ['16750', '38610', '55525', '30670', '49068'],
 ['21753', '54901', '54905', '44244', '19633'],
 ['14531', '3621', '13470', '44784', '19026'],
 ['3157', '5113', '3156', '3158', '5114'],
 ['24560', '36650', '55536', '36654', '25206'],
 ['36798', '15468', '31365', '38198', '38196'],
 ['35506', '22610', '9398', '46270', '52056'],
 ['21968', '21969', '12829', '23173', '21971'],
 ['6257', '22054', '20594', '45851', '8513'],
 ['27467', '2361', '4984', '56501', '48984'],
 ['19572', '18114', '44187', '19801', '18417'],
 ['8396', '22176', '39285', '53309', '37704'],
 ['15341', '53743', '53744', '56617', '54892'],
 ['7517', '7513', '7515', '7518', '7516'],
 ['46514', '15276', '43015', '36253', '36396'],
 ['5810', '445', '18620', '38162', '55777'],
 ['52367', '2360', '31577', '42554', '1066'],
 ['912', '4723', '50485', '39763', '46607'],
 ['2429', '5006', '41267', '6247', '40876'],
 ['904', '4721', '48386'

4. id에 맞는 context 가져오기

In [186]:
contexts = []
for i in range(len(l_id)):
    tmp = []
    for j in range(topk):
        tmp.append(id2context[l_id[i][j]])
    contexts.append(" ".join(tmp))
contexts

['순항 유도탄에 적용되는 추진기관은 일반적으로 생각하는 로켓이 사용되지 않는다. 이는 적으로부터 탐지되는 것을 사전에 방지코자 저고도 비행을 하는 순항 유도탄의 특성을 활용하여 공기흡입 추진기관을 사용하기 때문이다. 대표적으로 사용하는 추진기관은 터보계열 엔진으로 터보제트 엔진을 포함하여 터보팬 엔진 등이 사용되고 있다. 터보팬 엔진은 터보제트 엔진보다 큰 추력을 내는 데 효과적이다. 이는 연료 소모를 적게 하면서 흡입 공기의 유동으로 추력을 얻을 수 있기 때문인데, 상대적으로 팬 설치 등에 의한 흡입 전면면적의 확대가 필요하므로 큰 BPR은 순항 유도탄에는 적용이 제한적이다. 한편 순항 유도탄은 이음속으로 마하수 1 근처에서 비행하는 것이 통상적이나, 최근에는 초음속의 순항 유도탄이 개발 서비스되고 있어 새로운 추세로 보인다. 특히 러시아에서는 초음속 순항 유도탄에 기존의 터보계열 엔진에서 벗어나 액체 램제트 엔진을 사용하고 있다. 팰컨 9 우주 발사체의 최초 버전, 팰컨 9 1.0은 2005년 부터 2010년까지 5년간 개발된 소모성 우주 발사체 (ELV)이다. 2010년에 최초로 발사되었으며 은퇴하기 전까지 2010년부터 2013년간 총 5회 성공적으로 비행하였다.\n\n 팰컨 9 v1.0은 3X3 배열로 배치된 9개의 멀린 1C 엔진으로 작동되었다. 각각의 엔진은 abbr=in의 추력을 지녔고, 1단 추진체의 총 추력은 abbr=in이다.  팰컨 9 v1.0의 2단 추진체는 멀린 1C 진공 엔진 1기로 작동되었다. 기체 질소가 반응 억제제로 사용되었다. \n\n스페이스X는 두 단계 모두 재활용이 가능하기를 희망했으나,  낙하산을 사용한 1단 추진체의 회수 시도는 성공적이지 못했다.  로켓 착륙을 위한 새로운 디자인을 고안하면서 일론 머스크는 재사용 가능한 팰컨 9 로켓을 위한 모금활동을 활발하게 진행했다. 이문우는 경기도 이천에 있는 한 양반 천주교 집안에서 태어났다. 그는 다섯 살 때 부모를 여의었다. 한 매우 독실한 교우 여성이 그를 양자로 들여 

In [189]:
len(contexts)

595

# 설정한 m 값에 따라 앙상블 진행

test_true의 정답이 "2" 에서 만든 output파일에 포함되는지 여부를 계산하여 accuracy 계산

(test_true_youp.csv를 사용하면됨. 기존에 포함되지 않은 5개는 정답이 될 수 없음)

## true_test

In [17]:
from datasets import load_from_disk
import pandas as pd
# dataset = load_from_disk("../data/test_test")
dataset = load_from_disk("../data/test_true/test")

test_true = pd.DataFrame(dataset)
test_true.shape

(595, 9)

In [18]:
test_true.head()

title                                            context  \
0  더크 젠틀리의 성스러운 탐정 사무소  더크 젠틀리의 성스러운 탐정사무소의 줄거리는 이야기의 중추적인 부위에 자리잡은 시간...   
1               오퍼레이션7  냉전 종식 이후 전 세계적으로 소규모의 끊임없는 국지 분쟁들이 생겨나고 강대국들의 ...   
2            엥겔베르트 돌푸스  1933년 3월, 투표 과정의 위법성에 대한 문제제기가 불거졌다. 당시 오스트리아 ...   
3                  서구화  유럽인들의 아메리카와 오세아니아 식민지화로 인해 아메리카와 오세아니아의 문화적, 민...   
4                보응우옌잡  1926년 학생 시절 베트남청년혁명당에 가입했고 1930년에 학생 파업을 지지했다는...   

  news_category     source                       id  is_impossible  \
0          None  wikipedia    klue-mrc-v1_dev_00653          False   
1          None  wikipedia    klue-mrc-v1_dev_01113          False   
2          None  wikipedia  klue-mrc-v1_train_02191          False   
3          None  wikipedia  klue-mrc-v1_train_03951          False   
4          None  wikipedia    klue-mrc-v1_dev_01272          False   

   question_type                                 question  \
0              2                    유령'은 어느 행성에서 지구로 왔는가?   
1              1          용병회사의 경기가 좋아진 것은 무엇이 끝난 이후부터인가?   
2              1  돌푸스에게 불특정 기간동안 하원이 잠시 쉬는 것을 건의 받았던 인물은?   
3              1     마오리언어와 영어, 뉴질랜드 수화를 공식 언어로 사용하는 나라는?   
4              1               디엔비엔푸 전투에서 보응우옌잡이 상대한 국가는?   

                                         answers  
0       {'answer_start': [88], 'text': ['사락사라']}  
1          {'answer_start': [0], 'text': ['냉전']}  
2  {'answer_start': [253], 'text': ['빌헬름 미클라스']}  
3      {'answer_start': [645], 'text': ['뉴질랜드']}  
4       {'answer_start': [771], 'text': ['프랑스']}

## def ensemble()

In [26]:
def ensemble(df_l, topk):
    N = len(df_l)
    df_list = copy.deepcopy(df_l)
    # 1. 표준화
    for n in range(N):
        for i in range(df_list[n].shape[0]):
            tmp = df_list[n].iloc[i,]
            score = tmp[0:K]
            idx = tmp[K]
            # min-Max
            score_mM = (score - score.min()) / (score.max() - score.min())
            df_list[n].iloc[i,0:K] = score_mM
            # softmax
            df_list[n].iloc[i,0:K] = pd.Series(map(np.exp, score_mM)) / np.sum(pd.Series(map(np.exp, score_mM)))
            
    # 2. N개 데이터 합
    l_dict = []
    for i in range(df_list[0].shape[0]):
        tmp_dict = {}
        for j in range(N):
            idx = eval(df_list[j].iloc[i,K])
            for k in range(len(idx)):
                if idx[k] in tmp_dict.keys():
                    tmp_dict[idx[k]] += df_list[j].iloc[i,k]
                else:
                    tmp_dict[idx[k]] = df_list[j].iloc[i,k]
        l_dict.append(tmp_dict)
    
    # 3. query 별로 확률 높은 topk개의 id 반환
    l_id = []
    for i in range(len(l_dict)): # 595
        tmp = sorted(l_dict[i].items(), key = lambda x: x[1], reverse = True)[0:topk]
        ids = [x[0] for x in tmp]
        l_id.append(ids)
    
    # 4.id에 맞는 context 가져오기
    contexts = [] # 각 query에 대응하는 topk개의 context가 이어진 문자열들 리스트
    for i in range(len(l_id)):
        tmp = []
        for j in range(topk):
            tmp.append(id2context[int(l_id[i][j])])
        contexts.append(" ".join(tmp))
    
    # 5. accuracy 계산
    c =0
    ans = test_true['context']
    for i in range(len(contexts)):
            if ans[i] in contexts[i]: c+=1

    
    print(f"Accuracy: {c}/{len(test_true)} = {c/len(test_true)}")
    return contexts

# 앙상블!!

In [20]:
N = 9

In [24]:
k = 2

## m=1

In [25]:
m = 1
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 487/595 = 0.8184873949579832
           사용한 데이터 인덱스 : (0,)
Accuracy: 491/595 = 0.8252100840336134
           사용한 데이터 인덱스 : (1,)
Accuracy: 490/595 = 0.8235294117647058
           사용한 데이터 인덱스 : (2,)
Accuracy: 327/595 = 0.5495798319327732
           사용한 데이터 인덱스 : (3,)
Accuracy: 476/595 = 0.8
           사용한 데이터 인덱스 : (4,)
Accuracy: 449/595 = 0.7546218487394958
           사용한 데이터 인덱스 : (5,)
Accuracy: 450/595 = 0.7563025210084033
           사용한 데이터 인덱스 : (6,)
Accuracy: 460/595 = 0.773109243697479
           사용한 데이터 인덱스 : (7,)
----- 예외 발생 -----
           사용한 데이터 인덱스 : (8,)


## m=2

In [486]:
m = 2
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 489/595 = 0.8218487394957983
           사용한 데이터 인덱스 : (0, 1)
Accuracy: 488/595 = 0.8201680672268907
           사용한 데이터 인덱스 : (0, 2)
Accuracy: 454/595 = 0.7630252100840336
           사용한 데이터 인덱스 : (0, 3)
Accuracy: 484/595 = 0.8134453781512605
           사용한 데이터 인덱스 : (0, 4)
Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (0, 5)
Accuracy: 479/595 = 0.8050420168067227
           사용한 데이터 인덱스 : (0, 6)
Accuracy: 485/595 = 0.8151260504201681
           사용한 데이터 인덱스 : (0, 7)
Accuracy: 474/595 = 0.7966386554621848
           사용한 데이터 인덱스 : (0, 8)
Accuracy: 490/595 = 0.8235294117647058
           사용한 데이터 인덱스 : (1, 2)
Accuracy: 458/595 = 0.7697478991596639
           사용한 데이터 인덱스 : (1, 3)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (1, 4)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (1, 5)
Accuracy: 484/595 = 0.8134453781512605
           사용한 데이터 인덱스 : (1, 6)
Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (1, 7)
Accura

## m=3

In [489]:
m = 3
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 489/595 = 0.8218487394957983
           사용한 데이터 인덱스 : (0, 1, 2)
Accuracy: 477/595 = 0.8016806722689076
           사용한 데이터 인덱스 : (0, 1, 3)
Accuracy: 485/595 = 0.8151260504201681
           사용한 데이터 인덱스 : (0, 1, 4)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (0, 1, 5)
Accuracy: 485/595 = 0.8151260504201681
           사용한 데이터 인덱스 : (0, 1, 6)
Accuracy: 488/595 = 0.8201680672268907
           사용한 데이터 인덱스 : (0, 1, 7)
Accuracy: 487/595 = 0.8184873949579832
           사용한 데이터 인덱스 : (0, 1, 8)
Accuracy: 478/595 = 0.8033613445378152
           사용한 데이터 인덱스 : (0, 2, 3)
Accuracy: 485/595 = 0.8151260504201681
           사용한 데이터 인덱스 : (0, 2, 4)
Accuracy: 483/595 = 0.8117647058823529
           사용한 데이터 인덱스 : (0, 2, 5)
Accuracy: 487/595 = 0.8184873949579832
           사용한 데이터 인덱스 : (0, 2, 6)
Accuracy: 488/595 = 0.8201680672268907
           사용한 데이터 인덱스 : (0, 2, 7)
Accuracy: 486/595 = 0.8168067226890756
           사용한 데이터 인덱스 : (0, 2, 8)
Accuracy: 472/595 = 0.7932773109243697

## m=4

In [ ]:
m = 4
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 478/595 = 0.8033613445378152
           사용한 데이터 인덱스 : (0, 1, 2, 3)
Accuracy: 488/595 = 0.8201680672268907
           사용한 데이터 인덱스 : (0, 1, 2, 4)
Accuracy: 488/595 = 0.8201680672268907
           사용한 데이터 인덱스 : (0, 1, 2, 5)
Accuracy: 487/595 = 0.8184873949579832
           사용한 데이터 인덱스 : (0, 1, 2, 6)
Accuracy: 491/595 = 0.8252100840336134
           사용한 데이터 인덱스 : (0, 1, 2, 7)
Accuracy: 489/595 = 0.8218487394957983
           사용한 데이터 인덱스 : (0, 1, 2, 8)
Accuracy: 477/595 = 0.8016806722689076
           사용한 데이터 인덱스 : (0, 1, 3, 4)
Accuracy: 475/595 = 0.7983193277310925
           사용한 데이터 인덱스 : (0, 1, 3, 5)
Accuracy: 474/595 = 0.7966386554621848
           사용한 데이터 인덱스 : (0, 1, 3, 6)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (0, 1, 3, 7)
Accuracy: 476/595 = 0.8
           사용한 데이터 인덱스 : (0, 1, 3, 8)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (0, 1, 4, 5)
Accuracy: 483/595 = 0.8117647058823529
           사용한 데이터 인덱스 : (0, 1, 4, 6)
Accuracy: 488/

Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (2, 5, 6, 8)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (2, 5, 7, 8)
Accuracy: 482/595 = 0.8100840336134454
           사용한 데이터 인덱스 : (2, 6, 7, 8)
Accuracy: 455/595 = 0.7647058823529411
           사용한 데이터 인덱스 : (3, 4, 5, 6)
Accuracy: 473/595 = 0.7949579831932773
           사용한 데이터 인덱스 : (3, 4, 5, 7)
Accuracy: 475/595 = 0.7983193277310925
           사용한 데이터 인덱스 : (3, 4, 5, 8)
Accuracy: 473/595 = 0.7949579831932773
           사용한 데이터 인덱스 : (3, 4, 6, 7)
Accuracy: 474/595 = 0.7966386554621848
           사용한 데이터 인덱스 : (3, 4, 6, 8)
Accuracy: 478/595 = 0.8033613445378152
           사용한 데이터 인덱스 : (3, 4, 7, 8)
Accuracy: 463/595 = 0.7781512605042017
           사용한 데이터 인덱스 : (3, 5, 6, 7)


## m=5

In [ ]:
m = 5
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

## m=6

In [ ]:
m = 6
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

## m=7

In [ ]:
m = 7
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

## m=8

In [488]:
m = 8
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (0, 1, 2, 3, 4, 5, 6, 7)
Accuracy: 480/595 = 0.8067226890756303
           사용한 데이터 인덱스 : (0, 1, 2, 3, 4, 5, 6, 8)
Accuracy: 483/595 = 0.8117647058823529
           사용한 데이터 인덱스 : (0, 1, 2, 3, 4, 5, 7, 8)
Accuracy: 484/595 = 0.8134453781512605
           사용한 데이터 인덱스 : (0, 1, 2, 3, 4, 6, 7, 8)
Accuracy: 480/595 = 0.8067226890756303
           사용한 데이터 인덱스 : (0, 1, 2, 3, 5, 6, 7, 8)
Accuracy: 489/595 = 0.8218487394957983
           사용한 데이터 인덱스 : (0, 1, 2, 4, 5, 6, 7, 8)
Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (0, 1, 3, 4, 5, 6, 7, 8)
Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (0, 2, 3, 4, 5, 6, 7, 8)
Accuracy: 481/595 = 0.8084033613445378
           사용한 데이터 인덱스 : (1, 2, 3, 4, 5, 6, 7, 8)


## m=9

In [487]:
m = 9
comb = list(itertools.combinations(range(N), m))

for i in range(len(comb)):
    combination = comb[i]
    ldf = []
    for j in range(len(combination)):
        ldf.append(copy.deepcopy(df_list[combination[j]]))
    try:
        ensemble(ldf, k)
        print(f"           사용한 데이터 인덱스 : {combination}")
    except:
        print("----- 예외 발생 -----")
        print(f"           사용한 데이터 인덱스 : {combination}")

Accuracy: 483/595 = 0.8117647058823529
           사용한 데이터 인덱스 : (0, 1, 2, 3, 4, 5, 6, 7, 8)



# i
3

In [30]:
# idx = (1, 2, 4, 6, 8)
idx = (0, 2, 3, 4) # k=5

ldf = []
for i in idx:
    ldf.append(copy.deepcopy(df_list[i]))
len(ldf)

4

In [31]:
final = ensemble(ldf, 5)

Accuracy: 528/595 = 0.8873949579831932


In [29]:
len(final)

595

In [32]:
from datasets import load_from_disk
import pandas as pd
# dataset = load_from_disk("../data/train_dataset")
test_dataset=load_from_disk("../data/test_dataset")

# train_dataset = dataset["train"]
# valid_dataset = dataset["validation"]
test_dataset=test_dataset['validation']

# train_df=pd.DataFrame(train_dataset)
# valid_df=pd.DataFrame(valid_dataset)
test_df=pd.DataFrame(test_dataset)

In [33]:
text_final = []
fix = 0
for i in range(600):
    if i in [109, 198, 296, 418, 446]:
        text_final.append("nonetext")
        fix+=1
    else:
        text_final.append(final[i-fix])

In [34]:
d = {
    "question" : test_df['question'],
    "id" : test_df['id'],
    "context": text_final
}


In [37]:
df_final = pd.DataFrame(d)
df_final

question            id  \
0                           유령'은 어느 행성에서 지구로 왔는가?  mrc-1-000653   
1                 용병회사의 경기가 좋아진 것은 무엇이 끝난 이후부터인가?  mrc-1-001113   
2         돌푸스에게 불특정 기간동안 하원이 잠시 쉬는 것을 건의 받았던 인물은?  mrc-0-002191   
3            마오리언어와 영어, 뉴질랜드 수화를 공식 언어로 사용하는 나라는?  mrc-0-003951   
4                      디엔비엔푸 전투에서 보응우옌잡이 상대한 국가는?  mrc-1-001272   
..                                            ...           ...   
595                         타입 2 가이아 메모리을 만든 집단은?  mrc-0-002989   
596            장면이 정치보복에 반대하는 입장에서 처벌을 원치 않은 대상은?  mrc-0-001804   
597  콜드게임 중 어떠한 계기로 인해 잠시 중단된 뒤, 익일에 게임이 진행되는 것은?  mrc-0-003411   
598                            제2캐나다기갑여단이 상륙한 곳은?  mrc-0-003436   
599                     구립운석을 이루는 물질 중 널리 알려진 것은?  mrc-0-002605   

                                               context  
0    베피콜롬보\n베피콜롬보는 수성 탐사 계획 중 하나로 ESA와 JAXA가 공동으로 계...  
1    SK에서 방출된 이후 그는 일본을 여행하며 잠시 신변을 정리하고 있었다. 그 때 좌...  
2    1933년 3월, 투표 과정의 위법성에 대한 문제제기가 불거졌다. 당시 오스트리아 ...  
3    유럽인들의 아메리카와 오세아니아 식민지화로 인해 아메리카와 오세아니아의 문화적, 민...  
4    1926년 학생 시절 베트남청년혁명당에 가입했고 1930년에 학생 파업을 지지했다는...  
..                                                 ...  
595  재단 X가 슈라우드(=소노자키 후미네)가 개발한 가이아 메모리의 테크놀로지를 분석,...  
596  과거의 죄악에 대한 소급입법 적용을 반대하였다. 4.19 혁명 당시 사망한 사망자의...  
597  콜드게임(called game)이란 야구나 소프트볼 등의 운동경기에서 심판에 의하여...  
598  주노 해변\n\n주노 해변은 쿠르쇨르메르의 양쪽으로 뻗은 5마일 정도의 해변이었다....  
599  구립운석(球粒隕石, 콘드라이트)는 석질운석의 일종으로, 운석의 원석이 용융이나 분화...  

[600 rows x 3 columns]

In [41]:
test_true = pd.read_csv("../test_true_youp.csv")
test_true.head(1)

title                                            context  \
0  더크 젠틀리의 성스러운 탐정 사무소  더크 젠틀리의 성스러운 탐정사무소의 줄거리는 이야기의 중추적인 부위에 자리잡은 시간...   

  news_category     source                   guid is_impossible question_type  \
0           NaN  wikipedia  klue-mrc-v1_dev_00653         False             2   

                question                                   answers  
0  유령'은 어느 행성에서 지구로 왔는가?  {'answer_start': [88], 'text': ['사락사라']}

In [38]:
c =0
ans = test_true['context']
for i in range(600):
    if ans[i] in df_final['context'][i]: c+=1
c/595

0.8873949579831932

In [39]:
from datasets import concatenate_datasets, load_dataset, Dataset, DatasetDict
total_dataset = Dataset.from_pandas(df_final)
total_dataset.save_to_disk("retrieval_ensemble")